# Практикум 3

In [1]:
!pip install nglview 

/usr/lib/python3/dist-packages/secretstorage/dhcrypto.py:15: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
/usr/lib/python3/dist-packages/secretstorage/util.py:19: CryptographyDeprecationWarning: int_from_bytes is deprecated, use int.from_bytes instead
  from cryptography.utils import int_from_bytes
Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/usr/bin/python3 -m pip install --upgrade pip' command.


## Импортируем все необходимое

In [2]:
import nglview as nv
import requests         # Этот стандартный модуль позволяет посылать запросы к веб-ресурсам
import json             # Этот стандартный модуль позволяет легко работать с текстовым форматом json


## Задание 1

Мой вариант:

*   Ключевые слова: androgen receptor
*   Где они должны быть: В заголовке 
*   Какое разрешение: не хуже 2.5 ангстрем
*   Сколько лигандов должно быть в записи: не меньше 1
*   Дата публикации записи: с января 2000 по январь  2005 года

In [3]:
my_query = {
    "query": {
        "type": "group",
        "logical_operator": "and",
        "nodes": []
    },
    "return_type": "entry"
}

In [4]:
keyword_clause = {
    "type": "terminal",
    "service": "text", # Сервис поиска в определенном поле записи 
    "parameters": {
        "value": "androgen receptor", # Ключевое слово
        "attribute": "struct.title", # В данном случае это поле -- заголовок записи
        "operator": "contains_words" # Должны присутствовать какие-то слова
    }
}

my_query["query"]["nodes"].append(keyword_clause)

In [5]:
resolution_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "value": 2.5,  # Разрешение не хуже 2.5
        "attribute": "rcsb_entry_info.resolution_combined",
        "operator": "less_or_equal"
    }
}

my_query["query"]["nodes"].append(resolution_clause)

In [6]:
has_ligand_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_entry_info.nonpolymer_entity_count",
        "value": 0, # Число лигандов не меньше 1 
        "operator": "greater"
    }
}

my_query["query"]["nodes"].append(has_ligand_clause)

In [7]:
#  Дата публикации: с 1  января 2000 по 1 января 2005
date_range_clause = {
    "type": "terminal",
    "service": "text",
    "parameters": {
        "attribute": "rcsb_accession_info.initial_release_date",
        "value": {
            "from": "2000-01-01", 
            "to": "2005-01-01",
        },
        "operator": "range"
    }
}

my_query["query"]["nodes"].append(date_range_clause)

In [8]:
rcsb = 'https://search.rcsb.org/rcsbsearch/v1/query'

json_query = json.dumps(my_query) 

search = requests.post(f'{rcsb}', data=json_query) 

In [9]:
search 

<Response [200]>

In [10]:
search_result = search.json() 
search_result

{'query_id': 'ae556bde-f4c4-4191-9b98-bd278441255d',
 'result_type': 'entry',
 'total_count': 148,
 'result_set': [{'identifier': '1XOW',
   'score': 1.0,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 10707,
       'original_score': 262.7016906738281,
       'norm_score': 1.0}]}]},
  {'identifier': '1GS4',
   'score': 0.6283420021519527,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 10707,
       'original_score': 244.7921600341797,
       'norm_score': 0.6283420021519527}]}]},
  {'identifier': '1E3G',
   'score': 0.4488030950627315,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 10707,
       'original_score': 236.1405029296875,
       'norm_score': 0.4488030950627315}]}]},
  {'identifier': '1I37',
   'score': 0.2893407412520717,
   'services': [{'service_type': 'text',
     'nodes': [{'node_id': 10707,
       'original_score': 228.456298828125,
       'norm_score': 0.2893407412520717}]}]},
  {'identifier': '1XQ3',
   's

Лучший результат: 

In [11]:
best_hit = search_result["result_set"][0] 
best_hit

{'identifier': '1XOW',
 'score': 1.0,
 'services': [{'service_type': 'text',
   'nodes': [{'node_id': 10707,
     'original_score': 262.7016906738281,
     'norm_score': 1.0}]}]}

Таким образом, я далее буду работать с PDB ID 1XOW

## Задание 2. 





По индификатору 1XOW была найдена кристаллическая структура лиганд-связывающего домена рецептора андрогенов человека, связанного с NH2-концевым пептидом рецептора андрогенов, AR20-30 и R1881. 
Запись связана со статьей,  описывающий  роль рецептора  андрогена (AR) в  развитии  мужского пола и его способствование выживанию клеток рака предстательной железы. 

## Задание 3.

In [12]:
view = nv.show_pdbid('1XOW') #загрузка структуры молекулы
view

NGLWidget()

In [13]:
from ipywidgets import interact, fixed

In [14]:
my_examples = {
    'Example 3': {
        'description': '''
Белок в виде cartoon, покраска по типу вторичной структуры
Показана поверхность, с непрозрачностью 0.1
Лиганды в виде hyperball, покрашены в оттенок желтого 
''',
        'representations': [
                            {
                                "type": "cartoon", 
                           "params" : {"color":"sstruc", 
                                 "sele":"protein"}
                         },
                       
                         {"type":"hyperball",
                         "params": {"color":"yellow",
                                  "sele":"ligand"
                                   }
                       
                          },
                          {"type":"surface",
                           "params":{
                                    "sele":"protein",
                                    'opacity': 0.1}
                               
                          
                          
                          } 
                         ],
    },
    'Example 6': {
        'description': '''
Белок в виде cartoon темно-серого цвета
Боковые радикалы в виде линий светло-серого цвета
Боковые радикалы полярных аминокислот в виде hyperball, покрашены по элементам
Лиганды в шаростержневой модели, покрашены по элементам, углероды покрашены в темно-синий
''',
        'representations': [
            {
                'type': 'cartoon',                      
                'params': {
                    'sele': 'protein',               
                    'color': 'darkgray'  
                 }
            },
            {
                'type': 'line',                      
                'params': {
                    'sele': 'sidechain',                     
                    'color': 'lightgray'  
                 }
            },
            {
                'type': 'hyperball',                      
                'params': {
                    'sele': 'polar',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'ligand and _C',                     
                    'color': 'darkblue'  
                 }
            },
        ],
    },
    'Example 9': {
        'description': '''
Остов белка в шаростержневой модели, покрашен по элементам
Боковые радикалы в стержневой модели, покрашены по элементам
Углероды остатков с 30 по 70-й покрашены в светло-голубой
Лиганды показаны в виде линий, покрашены в любой оттенок оранжевого
''',
        'representations': [
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'backbone',               
                    'color': 'element'  
                 }
            },
            {
                'type': 'licorice',                      
                'params': {
                    'sele': 'sidechain',                     
                    'color': 'element'  
                 }
            },
            {
                'type': 'ball+stick',                      
                'params': {
                    'sele': 'protein and :A and 1030-1070 and _C',
                    'color': 'lightblue'  
                 }
            },
            {
                'type': 'line',
                'params': {
                    'sele': 'ligand',                     
                    'color': 'orange'  
                 }
            },
        ],
    },
}

In [15]:
def show_examples(view, example_name):
    view.clear()
    example = my_examples[example_name]
    print(example['description'])
    view.set_representations(example['representations'])
    view.center()

view = nv.show_pdbid("1XOW", default_representation=False)
interact(show_examples, view=fixed(view), example_name=list(my_examples.keys()))
view

interactive(children=(Dropdown(description='example_name', options=('Example 3', 'Example 6', 'Example 9'), va…

NGLWidget()